### 라이브러리 설치

In [332]:
from langchain_community.vectorstores import FAISS
from langchain_core.documents import Document
from langchain_openai import OpenAIEmbeddings
from langchain.embeddings import OpenAIEmbeddings
from langchain.vectorstores import FAISS
from dotenv import load_dotenv
from sklearn.feature_extraction.text import TfidfVectorizer
from transformers import pipeline
from sentence_transformers import SentenceTransformer

import numpy as np
import pandas as pd
import csv
import os

### 환경변수 및 api키 설정

In [333]:
# 환경변수 불러오기
load_dotenv()

True

In [334]:
# OpenAI API 키 설정 (환경 변수에서 가져오기)
openai_api_key = os.getenv('OPENAI_API_KEY')

#### File 불러오기

In [335]:
# 파일 경로 지정
df = pd.read_csv('정보통신산업진흥원_SW산업정보종합시스템 SW제품정보_20221031.csv',encoding='949')
df.head()

제품코드                       제품명  \
0  S202210222          드론관제영상 플랫폼(V1.0)   
1  S202210221  SkyRun 원격검침 통합관리 시스템 2.0   
2  S202210206                   ASM 5.1   
3  S202210201         아큐브 원격검침 시스템 v2.0   
4  S202210205          시큐웨이에스에스엘 유 V2.1   

                                                제품소개 운영환경  \
0  o 본 제품은 드론을 이용하여 촬영한 영상을 실시간으로 전송 받아 모니터링을 지원하...  NaN   
1  계량기에 연결된 단말기가 검침한 검침 값을 NBoIoT 통신을 통해 원격검침서버로 ...  NaN   
2    보안 에이전트가 설치된 PC를 관리하고, 정책 적용을 수행하는 통합 중앙 관리 솔루션  NaN   
3  IoT 통신을 통해 수도 사용 정보를 확인하고 점검하기 위한 수도 원격 검침 관리 ...  NaN   
4  외부 네트워크 사용자가 암호화된 통신 채널을 통해 내부 네트워크 시스템에 접속할 수...  NaN   

                                                주요기능 특징 및 장점         회사명 홈페이지  
0  1) 수신 영상 출력 : Wowza Streaming Engine으로부터 수신한 드...     NaN  유콘시스템 주식회사  NaN  
1  1) SkyRun 원격검침 통합관리 WEB 2.0o 대시보드를 이용한 사용량, 장비...     NaN  (주) 하이텍이피씨  NaN  
2          o 악성 코드 탐지 및 대응o 보안 정책 설정 및 관리o 에이전트 관리 등     NaN    ㈜이스트시큐리티  NaN  
3                수도 실시간 현황 조회수도 누수 점검 관리수용가 및 계량기 관리     NaN    ㈜케이스마트피아  NaN  
4  o 클라이언트(Windows, Embedded Linux, Android) 접근 제...     NaN       ㈜시큐위즈  NaN

### 데이터 전처리

In [336]:
# 불필요 컬럼 제거 및 결측치 처리
df = df.drop(['제품코드', '홈페이지', '운영환경'], axis=1)
df = df.fillna('')

In [337]:
# 불필요 방해 단어 제거
df['제품소개'] = df['제품소개'].str.replace('o ', ' ')
df['주요기능'] = df['주요기능'].str.replace('o ', ' ')

In [338]:
# # 데이터 중복 제거
# df = df.drop_duplicates()

In [339]:
df.head()

제품명  \
0          드론관제영상 플랫폼(V1.0)   
1  SkyRun 원격검침 통합관리 시스템 2.0   
2                   ASM 5.1   
3         아큐브 원격검침 시스템 v2.0   
4          시큐웨이에스에스엘 유 V2.1   

                                                제품소개  \
0   본 제품은 드론을 이용하여 촬영한 영상을 실시간으로 전송 받아 모니터링을 지원하는...   
1  계량기에 연결된 단말기가 검침한 검침 값을 NBoIoT 통신을 통해 원격검침서버로 ...   
2    보안 에이전트가 설치된 PC를 관리하고, 정책 적용을 수행하는 통합 중앙 관리 솔루션   
3  IoT 통신을 통해 수도 사용 정보를 확인하고 점검하기 위한 수도 원격 검침 관리 ...   
4  외부 네트워크 사용자가 암호화된 통신 채널을 통해 내부 네트워크 시스템에 접속할 수...   

                                                주요기능 특징 및 장점         회사명  
0  1) 수신 영상 출력 : Wowza Streaming Engine으로부터 수신한 드...          유콘시스템 주식회사  
1  1) SkyRun 원격검침 통합관리 WEB 2.0 대시보드를 이용한 사용량, 장비 ...          (주) 하이텍이피씨  
2              악성 코드 탐지 및 대응 보안 정책 설정 및 관리 에이전트 관리 등            ㈜이스트시큐리티  
3                수도 실시간 현황 조회수도 누수 점검 관리수용가 및 계량기 관리            ㈜케이스마트피아  
4   클라이언트(Windows, Embedded Linux, Android) 접근 제어...               ㈜시큐위즈

#### CSV 파일 Page 별 Split

In [340]:
# 행별로 리스트화
df_list = df.values.tolist()

# 결과 확인
for row in df_list:
    print(row)

['드론관제영상 플랫폼(V1.0)', ' 본 제품은 드론을 이용하여 촬영한 영상을 실시간으로 전송 받아 모니터링을 지원하는 소프트웨어   ※ 드론으로부터 영상은 “Wowza Streaming Engine” 소프트웨어가 수신하여 본 제품으로 재전송함. 재전송 받은 영상을 웹 환경에서 확인할 수 있도록 출력.', '1) 수신 영상 출력 : Wowza Streaming Engine으로부터 수신한 드론 영상 출력(1분할/4분할)2) 사용자 관리 : 사용자 계정 관리 및 로그인 이력', '', '유콘시스템 주식회사']
['SkyRun 원격검침 통합관리 시스템 2.0', '계량기에 연결된 단말기가 검침한 검침 값을 NBoIoT 통신을 통해 원격검침서버로 전송하고장비(단말기 및 계량기) 및 수용가 관리 기능과 검침정보를 제공하는 소프트웨어', '1) SkyRun 원격검침 통합관리 WEB 2.0 대시보드를 이용한 사용량, 장비 현황, 통신 및 검침 상태 통합모니터링 기능 계량기 교체이력 관리 및 수용가의 누수 여부 확인 기능 지도 서비스를 이용한 단말기의 상태정보 및 설치위치 확인 기능 수용가의 시간별, 일별, 월별 사용량 통계 정보 제공 기능 수용가, 단말기 및 계량기에 대한 정보 등록, 수정 및 삭제 기능2) SkyRun 원격검침 통합관리 펌웨어 2.0 계량기의 검침 값과 단말기 상태 정보를 LG 유플러스 oneM2M 플랫폼을 통하여 원격검침서버로 전송', '', '(주) 하이텍이피씨']
['ASM 5.1', '보안 에이전트가 설치된 PC를 관리하고, 정책 적용을 수행하는 통합 중앙 관리 솔루션', ' 악성 코드 탐지 및 대응 보안 정책 설정 및 관리 에이전트 관리 등', '', '㈜이스트시큐리티']
['아큐브 원격검침 시스템 v2.0', 'IoT 통신을 통해 수도 사용 정보를 확인하고 점검하기 위한 수도 원격 검침 관리 프로그램', '수도 실시간 현황 조회수도 누수 점검 관리수용가 및 계량기 관리', '', '㈜케이스마트피아']
['시큐웨이에스에스엘 유 V2.1', '

### csv -> 다큐먼트 형식으로 변환

In [341]:
# 각 행을 청크로 나누기 및 다큐먼트 형식으로 변환
def split_row_into_chunks(row, max_length=1000):
    row_text = ' '.join(row)
    words = row_text.split()
    return [' '.join(words[i:i + max_length]) for i in range(0, len(words), max_length)]

documents = []
for row in df_list:
    chunks = split_row_into_chunks(row)
    row_documents = [Document(page_content=chunk) for chunk in chunks]
    documents.extend(row_documents)

In [331]:
documents

[Document(page_content='드론관제영상 플랫폼(V1.0) 본 제품은 드론을 이용하여 촬영한 영상을 실시간으로 전송 받아 모니터링을 지원하는 소프트웨어 ※ 드론으로부터 영상은 “Wowza Streaming Engine” 소프트웨어가 수신하여 본 제품으로 재전송함. 재전송 받은 영상을 웹 환경에서 확인할 수 있도록 출력. 1) 수신 영상 출력 : Wowza Streaming Engine으로부터 수신한 드론 영상 출력(1분할/4분할)2) 사용자 관리 : 사용자 계정 관리 및 로그인 이력 유콘시스템 주식회사'),
 Document(page_content='SkyRun 원격검침 통합관리 시스템 2.0 계량기에 연결된 단말기가 검침한 검침 값을 NBoIoT 통신을 통해 원격검침서버로 전송하고장비(단말기 및 계량기) 및 수용가 관리 기능과 검침정보를 제공하는 소프트웨어 1) SkyRun 원격검침 통합관리 WEB 2.0 대시보드를 이용한 사용량, 장비 현황, 통신 및 검침 상태 통합모니터링 기능 계량기 교체이력 관리 및 수용가의 누수 여부 확인 기능 지도 서비스를 이용한 단말기의 상태정보 및 설치위치 확인 기능 수용가의 시간별, 일별, 월별 사용량 통계 정보 제공 기능 수용가, 단말기 및 계량기에 대한 정보 등록, 수정 및 삭제 기능2) SkyRun 원격검침 통합관리 펌웨어 2.0 계량기의 검침 값과 단말기 상태 정보를 LG 유플러스 oneM2M 플랫폼을 통하여 원격검침서버로 전송 (주) 하이텍이피씨'),
 Document(page_content='ASM 5.1 보안 에이전트가 설치된 PC를 관리하고, 정책 적용을 수행하는 통합 중앙 관리 솔루션 악성 코드 탐지 및 대응 보안 정책 설정 및 관리 에이전트 관리 등 ㈜이스트시큐리티'),
 Document(page_content='아큐브 원격검침 시스템 v2.0 IoT 통신을 통해 수도 사용 정보를 확인하고 점검하기 위한 수도 원격 검침 관리 프로그램 수도 실시간 현황 조회수도 누수 점검 관리수용가 및 계량기 관

#### Local FAISS에 Chunk 저장

In [ ]:
# 벡터 db 생성
embedding_model = OpenAIEmbeddings()
vectorstore = FAISS.from_documents(documents=documents, embedding=embedding_model)

# 로컬에 db 저장
vectorstore.save_local('./db/faiss')